In [1]:
%pip install pandas requests psycopg2-binary jupyter


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
%pip install pandas requests psycopg2-binary jupyter


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: python -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [3]:
import requests
import pandas as pd

In [4]:
# Se configura API Key
api_key = "dd4e52a0-f2f8-4cdd-8d6d-03febbef0963"
url = "https://services.nvd.nist.gov/rest/json/cves/2.0"
params = {
    "resultsPerPage": 10,
    "apiKey": api_key
}

In [5]:
# Se realiza la solicitud
response = requests.get(url, params=params)

In [6]:
# Diagnóstico
print("Código de estado:", response.status_code)
print("Encabezados:", response.headers)
print("Contenido crudo:", response.text)

Código de estado: 404
Encabezados: {'message': 'Invalid parameter: apiKey.', 'x-frame-options': 'SAMEORIGIN', 'access-control-allow-origin': '*', 'access-control-allow-headers': 'accept, apiKey, content-type, origin, x-requested-with', 'access-control-allow-methods': 'GET, HEAD, OPTIONS', 'access-control-allow-credentials': 'false', 'date': 'Sun, 23 Feb 2025 16:03:39 GMT', 'content-length': '0', 'apikey': 'Yes', 'strict-transport-security': 'max-age=31536000'}
Contenido crudo: 


In [10]:
import requests
import time

# Dado que salió error 404, se validó que se debería probar sin el uso de params, a continuación se ejecuta el código desde cero.
api_key = "dd4e52a0-f2f8-4cdd-8d6d-03febbef0963"
url = "https://services.nvd.nist.gov/rest/json/cves/2.0"
params = {
    "resultsPerPage": 10,
    "apiKey": api_key
}
headers = {"Accept": "application/json"}

# Retraso por si hay límites de tasa
time.sleep(1)

# Intento 1: Solicitud con params
response = requests.get(url, params=params, headers=headers)
print("Intento 1 - Código:", response.status_code)
print("Intento 1 - URL:", response.url)
print("Intento 1 - Texto:", response.text)

# Intento 2: Sin parámetros 
if response.status_code == 404:
    response = requests.get(url, headers=headers)
    print("\nIntento 2 (sin params) - Código:", response.status_code)
    print("Intento 2 - Texto:", response.text)
    # Procesa los datos si es exitoso
if response.status_code == 200:
    data = response.json()  # Define 'data' aquí
    # Se extrae los CVEs
    cves = data["vulnerabilities"]  # Ahora 'data' existe
    print("Número de CVEs obtenidos:", len(cves))
    print("Primer CVE:", cves[0])  # Muestra el primer elemento para verificar
else:
    print("Error:", response.text)

Intento 1 - Código: 404
Intento 1 - URL: https://services.nvd.nist.gov/rest/json/cves/2.0?resultsPerPage=10&apiKey=dd4e52a0-f2f8-4cdd-8d6d-03febbef0963
Intento 1 - Texto: 

Intento 2 (sin params) - Código: 200
Intento 2 - Texto: {"resultsPerPage":2000,"startIndex":0,"totalResults":282102,"format":"NVD_CVE","version":"2.0","timestamp":"2025-02-23T16:13:57.203","vulnerabilities":[{"cve":{"id":"CVE-1999-0095","sourceIdentifier":"cve@mitre.org","published":"1988-10-01T04:00:00.000","lastModified":"2024-11-20T23:27:50.607","vulnStatus":"Modified","cveTags":[],"descriptions":[{"lang":"en","value":"The debug command in Sendmail is enabled, allowing attackers to execute commands as root."},{"lang":"es","value":"El comando de depuración de Sendmail está activado, permitiendo a atacantes ejecutar comandos como root."}],"metrics":{"cvssMetricV2":[{"source":"nvd@nist.gov","type":"Primary","cvssData":{"version":"2.0","vectorString":"AV:N\/AC:L\/Au:N\/C:C\/I:C\/A:C","baseScore":10.0,"accessVector":"

In [14]:
import requests
import pandas as pd

# Se valida que el código debe ejecutarse totalmente, tomamos la configuración realizada con el API key que proporcionó NIST
url = "https://services.nvd.nist.gov/rest/json/cves/2.0"
headers = {"Accept": "application/json"}
api_key = "dd4e52a0-f2f8-4cdd-8d6d-03febbef0963"
params = {
    "resultsPerPage": 10,
    "apiKey": api_key
}

# Realizamos la solicitud
response = requests.get(url, params=params, headers=headers)
if response.status_code == 404:
    print("Parámetros fallaron, intentando sin ellos...")
    response = requests.get(url, headers=headers)

# Se procesan los datos una vez hayamos obtenido status 200
if response.status_code == 200:
    data = response.json()
    cves = data["vulnerabilities"][:10]  # Limita a 10 filas
    print("Número de CVEs obtenidos:", len(cves))  # Verifica cuántas filas hay

    # Seleccionamos las 5 columnas útiles
    df = pd.DataFrame([
        {
            "cve_id": cve["cve"]["id"],
            "description": cve["cve"]["descriptions"][0]["value"],
            "published": cve["cve"]["published"],
            "last_modified": cve["cve"]["lastModified"],
            "severity": cve["cve"]["metrics"]["cvssMetricV31"][0]["cvssData"]["baseSeverity"] if "cvssMetricV31" in cve["cve"]["metrics"] else "N/A"
        }
        for cve in cves
    ])
    # Se muestra el DataFrame completo (10 filas)
    print("Datos extraídos (10 filas):")
    print(df)  # Se utiliza print(df) en lugar de df.head() para mostrar todas las filas
else:
    print("Error:", response.status_code, response.text)

Parámetros fallaron, intentando sin ellos...
Número de CVEs obtenidos: 10
Datos extraídos (10 filas):
          cve_id                                        description  \
0  CVE-1999-0095  The debug command in Sendmail is enabled, allo...   
1  CVE-1999-0082      CWD ~root command in ftpd allows root access.   
2  CVE-1999-1471  Buffer overflow in passwd in BSD based operati...   
3  CVE-1999-1122  Vulnerability in restore in SunOS 4.0.3 and ea...   
4  CVE-1999-1467  Vulnerability in rcp on SunOS 4.0.x allows rem...   
5  CVE-1999-1506  Vulnerability in SMI Sendmail 4.0 and earlier,...   
6  CVE-1999-0084  Certain NFS servers allow users to use mknod t...   
7  CVE-2000-0388  Buffer overflow in FreeBSD libmytinfo library ...   
8  CVE-1999-0209  The SunView (SunTools) selection_svc facility ...   
9  CVE-1999-1198  BuildDisk program on NeXT systems before 2.0 d...   

                 published            last_modified severity  
0  1988-10-01T04:00:00.000  2024-11-20T23:27:50.607  